In [1]:
import torch
import gpytorch
from botorch.models import SingleTaskGP
from botorch.acquisition.analytic import ExpectedImprovement
from botorch.models.transforms.outcome import Standardize
from gpytorch.kernels import ScaleKernel
from gpytorch.mlls import ExactMarginalLogLikelihood
from botorch import fit_gpytorch_model
from botorch.optim.fit import fit_gpytorch_torch # fix Cholecky jitter error
from scipy.stats import norm
from sklearn.decomposition import PCA
import math 
import numpy as np
import matplotlib.pyplot as plt
import h5py
import pickle
import os
import time

# config plot settings
plt.rcParams["font.size"] = 16

## Load Data

In [ ]:
normalization = "min_max_normalization" # "standardization"

In [ ]:
###
#  load data: targets and features
###
if normalization == 'min_max_normalization':
    file = h5py.File("targets_and_normalized_features.jld2", "r")
else:
    file = h5py.File("targets_and_standardized_features.jld2", "r")

# feature matrix
X = torch.from_numpy(np.transpose(file["X"][:]))
# simulation data (high fidelity)
y = torch.from_numpy(np.transpose(file["gcmc_y"][:]))
# associated simulation costs
cost = torch.from_numpy(np.transpose(file["gcmc_elapsed_time"][:]))

# total number of COFs in data set
nb_COFs = X.shape[0]

In [2]:
###
#  load data: initializing COFs
###
init_cof_ids_file = pickle.load(open('search_results/{}/initializing_cof_ids.pkl'.format(normalization), 'rb'))
init_cof_ids = init_cof_ids_file['init_cof_ids']

# total number of BO searches to run = number of initializing sets
nb_runs = len(init_cof_ids)

###
#  print info
###
print("raw data - \n\tX:", X.shape)
print("\t\ty:", y.shape)
print("\t\tcost: ", cost.shape)    
    
print("\nEnsure features are normalized - ")
print("max:\n", torch.max(X, 0).values)
print("min:\n", torch.min(X, 0).values)
print("width:\n",torch.max(X, 0).values - torch.min(X, 0).values)

raw data - 
	X: torch.Size([608, 14])
		y: torch.Size([608])
		cost:  torch.Size([608])

Ensure features are normalized - 
max:
 tensor([0.7144, 0.4136, 0.4696, 0.6677, 0.9579, 0.8383, 0.3595, 0.3207, 0.9938,
        0.8242, 0.9692, 0.9869, 0.9868, 0.9762], dtype=torch.float64)
min:
 tensor([-0.2856, -0.5864, -0.5304, -0.3323, -0.0421, -0.1617, -0.6405, -0.6793,
        -0.0062, -0.1758, -0.0308, -0.0131, -0.0132, -0.0238],
       dtype=torch.float64)
width:
 tensor([1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000,
        1.0000, 1.0000, 1.0000, 1.0000, 1.0000], dtype=torch.float64)


In [3]:
X_unsqueezed = X.unsqueeze(1)

## Helper Functions

#### Analysis

In [4]:
# accumulated cost lags the index of the cost_acquired (iteration COF is identified) by 1
def accumulated_cost(cost_acquired):
    nb_iters = len(cost_acquired)
    accumulated_cost = np.zeros(nb_iters)
    accumulated_cost[0] = cost_acquired[0]
    for i in range(1, len(cost_acquired)):
        accumulated_cost[i] = accumulated_cost[i-1] + cost_acquired[i]
    return accumulated_cost

In [5]:
def get_y_maxes_acquired(y_acquired):
    nb_iters = len(y_acquired)
    return [max(y_acquired[:i+1]) for i in range(nb_iters)]      

#### Construct Initial Inputs

In [6]:
# construct feature matrix of acquired points
def build_X_train(ids_acquired):
    return X[ids_acquired, :]

# construct output vector for acquired points
def build_y_train(ids_acquired):
    return y[ids_acquired].unsqueeze(-1)

# construct vector to track accumulated cost of acquired points
def build_cost(ids_acquired):
    return cost[ids_acquired]

In [7]:
# construct and fit GP model
def construct_and_fit_gp_model(X_train, y_train):      
    model = SingleTaskGP(X_train, y_train, outcome_transform=Standardize(m=1))
    mll   = ExactMarginalLogLikelihood(model.likelihood, model)
    fit_gpytorch_model(mll, optimizer=fit_gpytorch_torch)
    return model

#### Bayesian Algorithm

In [8]:
def run_Bayesian_optimization(nb_iterations, initializing_COFs, verbose=False):
    assert nb_iterations > len(initializing_COFs)
    ###
    #  initialize system
    ###
    # select initial COFs for training data
    ids_acquired = initializing_COFs
    
    ###
    #  itterate through remaining budget using BO
    ###
    for i in range(len(initializing_COFs), nb_iterations):
        # construct training data (perform experiments)
        X_train = build_X_train(ids_acquired)
        y_train = build_y_train(ids_acquired)
        
        # fit GP surrogate model
        model = construct_and_fit_gp_model(X_train, y_train)
        
        # compute expected improvement acquisition function
        acq_fn   = ExpectedImprovement(model, best_f=y_train.max().item())
        acq_vals = acq_fn.forward(X.unsqueeze(1))
        
        # identify COF with highest acquisition value currently *not* in training set
        ids_sorted_by_aquisition = acq_vals.argsort(descending=True)
        for id_max in ids_sorted_by_aquisition:
            if not id_max.item() in ids_acquired:
                id_max_acq = id_max.item()
                break
                
        ###
        #  acquire this COF
        ###
        ids_acquired = np.concatenate((ids_acquired, [id_max_acq]))
        if verbose:
            print("BO iteration ", i)
            print("\tacquired COF ", id_max_acq)
            print("\ty = ", y[id_max_acq].item())
    
    # check budget constraint is stisfied
    assert np.size(ids_acquired) == nb_iterations
    assert len(np.unique(ids_acquired)) == nb_iterations
    return ids_acquired

# Run BO

In [10]:
nb_iterations = 150
nb_COFs_initialization = 3

In [9]:
for i, initializing_COFs in enumerate(init_cof_ids): 
    # check the length of each initializing set
    assert len(initializing_COFs) == nb_COFs_initialization
    print("run #: {}".format(i))
    
    # start timer for BO run
    start_time    = time.time()
    ###
    #  run BO search
    ###
    ids_acquired  = run_Bayesian_optimization(nb_iterations, initializing_COFs)
    
    ###
    #  post-run analysis
    ###
    elapsed_time  = time.time() - start_time
    y_acquired    = y[ids_acquired]
    y_maxes_acq   = get_y_maxes_acquired(y_acquired.detach().numpy())
    cost_acquired = build_cost(ids_acquired)
    acc_cost      = accumulated_cost(cost_acquired.detach().numpy())
        
    BO_iter_top_cof_acquired = np.argmax(y_acquired == max(y))
    print("iteration we acquire top COF = ", BO_iter_top_cof_acquired.item())
    
    top_cof_acc_cost = sum(cost_acquired[:BO_iter_top_cof_acquired]).item() 
    print("accumulated cost up to observation of top COF = ", top_cof_acc_cost, " [min]")
    
    ###
    #  Store SFBO results
    ###
    sfbo_res = dict({'ids_acquired': ids_acquired,
                     'y_acquired': y_acquired.detach().numpy(),
                     'y_max_acquired': y_maxes_acq,
                     'cost_acquired': cost_acquired.detach().numpy(),
                     'accumulated_cost': acc_cost / 60,
                     'nb_COFs_initialization': nb_COFs_initialization,
                     'BO_iter_top_cof_acquired': BO_iter_top_cof_acquired.item(),
                     'elapsed_time (min)':  elapsed_time / 60
                    })

    with open('search_results/{}/sfbo_results/sfbo_results_run_{}.pkl'.format(normalization, i), 'wb') as file:
        pickle.dump(sfbo_res, file)

run #: 0
Iter 10/100: 2.5316478673813574
Iter 20/100: 1.5976805610155178
Iter 30/100: 1.5335137562067445
Iter 40/100: 1.5103225146173305
Iter 50/100: 1.4670837577792153
Iter 60/100: 1.4641026733095588
Iter 10/100: 2.2821451376626243
Iter 20/100: 1.576745767814489
Iter 30/100: 1.516054702172481
Iter 40/100: 1.4776026924306396
Iter 50/100: 1.4418954556648251
Iter 60/100: 1.43763657751167
Iter 10/100: 2.1182714695918206
Iter 20/100: 1.5406069636537971
Iter 30/100: 1.465887253647115
Iter 40/100: 1.4001012223371432
Iter 50/100: 1.3578769891536706
Iter 60/100: 1.3454021759424304
Iter 10/100: 2.0287369141547815
Iter 20/100: 1.5417800785110842
Iter 30/100: 1.4659487823993385
Iter 40/100: 1.4034512338980265
Iter 50/100: 1.3717580593803287
Iter 60/100: 1.361105079632785
Iter 70/100: 1.3618015872844438
Iter 80/100: 1.36018918191592
Iter 10/100: 1.9589766650408083
Iter 20/100: 1.5326601154524975
Iter 30/100: 1.4491168836714323
Iter 40/100: 1.445171349151378
Iter 10/100: 1.9072783848615875
Iter 20/

Iter 30/100: 1.3687613845757467
Iter 40/100: 1.3172891526987183
Iter 50/100: 1.2589463442746147
Iter 10/100: 1.5444253709030695
Iter 20/100: 1.4236633049139633
Iter 30/100: 1.3671616662060808
Iter 40/100: 1.314080008464378
Iter 50/100: 1.2566686405552339
Iter 10/100: 1.5423900014111913
Iter 20/100: 1.422222816300868
Iter 30/100: 1.3645924711059507
Iter 40/100: 1.3100767062774745
Iter 50/100: 1.2527341802884135
Iter 10/100: 1.5404041000099926
Iter 20/100: 1.4209181826559412
Iter 30/100: 1.3623012147622664
Iter 40/100: 1.3063455251210148
Iter 50/100: 1.2494507089836828
Iter 10/100: 1.5379613720423508
Iter 20/100: 1.4190283002514157
Iter 30/100: 1.359212622452353
Iter 40/100: 1.3016165536613369
Iter 50/100: 1.2437149578292694
Iter 10/100: 1.536703061724202
Iter 20/100: 1.4183546546733552
Iter 30/100: 1.3579886289987781
Iter 40/100: 1.298744937152933
Iter 50/100: 1.2380378132433796
Iter 10/100: 1.5340263931052285
Iter 20/100: 1.4158425141774666
Iter 30/100: 1.3542096266138755
Iter 40/100: 

Iter 70/100: 1.1703414796196026
Iter 80/100: 1.1700283735380432
Iter 90/100: 1.1696136413897409
Iter 10/100: 1.4937079718043298
Iter 20/100: 1.3818096124536603
Iter 30/100: 1.2943058128872778
Iter 40/100: 1.2250199737191854
Iter 50/100: 1.188954385246289
Iter 60/100: 1.1706289474129787
Iter 70/100: 1.1676016375333966
Iter 80/100: 1.167335641410277
Iter 90/100: 1.1669326932231732
Iter 10/100: 1.4927530161180766
Iter 20/100: 1.3810419968808336
Iter 30/100: 1.2929517486195121
Iter 40/100: 1.2228754688472872
Iter 50/100: 1.186697295501553
Iter 60/100: 1.1690803670768513
Iter 70/100: 1.1659218254310164
Iter 80/100: 1.1655790529204666
Iter 90/100: 1.165146214964255
Iter 100/100: 1.1649500958406456
Iter 10/100: 1.4899317006273145
Iter 20/100: 1.377228148138116
Iter 30/100: 1.2858078418299719
Iter 40/100: 1.2110170723518576
Iter 50/100: 1.1728494716676159
Iter 60/100: 1.1524437909217975
Iter 70/100: 1.1488700581105182
Iter 10/100: 1.488540016927496
Iter 20/100: 1.375749474575904
Iter 30/100: 1

Iter 50/100: 1.0702542828570578
Iter 60/100: 1.064457276978592
Iter 70/100: 1.061424026846409
Iter 80/100: 1.0609292980954157
Iter 10/100: 1.4560617746781819
Iter 20/100: 1.338556316393663
Iter 30/100: 1.2145748052336385
Iter 40/100: 1.0984622280184702
Iter 50/100: 1.0672150951544581
Iter 60/100: 1.0614831775251248
Iter 70/100: 1.058407457146649
Iter 80/100: 1.0579021221692821
Iter 10/100: 1.4547586670043289
Iter 20/100: 1.33700865945011
Iter 30/100: 1.2120746121489663
Iter 40/100: 1.0946738599747956
Iter 50/100: 1.0631071339717897
Iter 60/100: 1.0573472746504138
Iter 70/100: 1.0541547128802884
Iter 80/100: 1.0536103000580883
Iter 10/100: 1.4541980641037537
Iter 20/100: 1.3363642851504227
Iter 30/100: 1.2105567422638273
Iter 40/100: 1.091886448798902
Iter 50/100: 1.0604534590061765
Iter 60/100: 1.0546421968563773
Iter 70/100: 1.0515750766667702
Iter 80/100: 1.0511113470709295
Iter 10/100: 1.4536660880657883
Iter 20/100: 1.335724425750778
Iter 30/100: 1.2090938395725535
Iter 40/100: 1.0

Iter 50/100: 1.3354856843692293
Iter 60/100: 1.3257140369810567
Iter 70/100: 1.3244978080614014
Iter 80/100: 1.3242479858101468
Iter 90/100: 1.324153029104674
Iter 10/100: 1.7891492441169492
Iter 20/100: 1.4749067242696157
Iter 30/100: 1.3591093391136904
Iter 40/100: 1.2388556460595257
Iter 10/100: 1.7594417392235309
Iter 20/100: 1.4626994690365294
Iter 30/100: 1.3449873505906982
Iter 40/100: 1.241439039737048
Iter 10/100: 1.7470769116980434
Iter 20/100: 1.4630324196997992
Iter 30/100: 1.3501255728781971
Iter 40/100: 1.255155369259171
Iter 10/100: 1.7327673914344424
Iter 20/100: 1.4647572388417678
Iter 30/100: 1.35911645039287
Iter 40/100: 1.3079737172917127
Iter 10/100: 1.7194600989384499
Iter 20/100: 1.4633884677188005
Iter 30/100: 1.3588714076635953
Iter 40/100: 1.3206016308884876
Iter 10/100: 1.7031816521115029
Iter 20/100: 1.457322528575974
Iter 30/100: 1.3510721445336387
Iter 40/100: 1.3087709563886305
Iter 10/100: 1.702518497050473
Iter 20/100: 1.4841897030131213
Iter 30/100: 1.

...

Iter 70/100: 1.0536589855733083
Iter 80/100: 1.0528762697639025
Iter 90/100: 1.052495913973182
Iter 10/100: 1.4494600927569483
Iter 20/100: 1.3304870901955466
Iter 30/100: 1.1994601855563984
Iter 40/100: 1.076910561397672
Iter 50/100: 1.0460677335132078
Iter 60/100: 1.0396051943675229
Iter 70/100: 1.037952469974745
Iter 80/100: 1.0374299768836253
Iter 90/100: 1.0370160022257053
Iter 10/100: 1.4493147638729496
Iter 20/100: 1.330440067013934
Iter 30/100: 1.1994291998856563
Iter 40/100: 1.075696960985001
Iter 50/100: 1.044082546195767
Iter 60/100: 1.0374783396522222
Iter 70/100: 1.0356628290278516
Iter 80/100: 1.035156781592982
Iter 90/100: 1.0347967126945163
Iter 10/100: 1.4493335440451172
Iter 20/100: 1.3306568091284374
Iter 30/100: 1.1997713784235269
Iter 40/100: 1.0751754340634097
Iter 50/100: 1.0434850974582266
Iter 60/100: 1.0369644855948763
Iter 70/100: 1.0351783268854415
Iter 80/100: 1.0346589952770553
Iter 90/100: 1.034287730000024
Iter 10/100: 1.4487269550860316
Iter 20/100: 1.3

Iter 10/100: 1.630002892350636
Iter 20/100: 1.4508944983985748
Iter 30/100: 1.3704832677849643
Iter 40/100: 1.2591817258486442
Iter 10/100: 1.6383653185180678
Iter 20/100: 1.4660679515553954
Iter 30/100: 1.4126376623099284
Iter 40/100: 1.3622877933512552
Iter 50/100: 1.3304820912748674
Iter 10/100: 1.6340424751470217
Iter 20/100: 1.4656552477855447
Iter 30/100: 1.4151553278444242
Iter 40/100: 1.3692278378081528
Iter 50/100: 1.3321426248788661
Iter 10/100: 1.6288860969177317
Iter 20/100: 1.4640873547233337
Iter 30/100: 1.4148110211144154
Iter 40/100: 1.3704350087315906
Iter 50/100: 1.3486971880296654
Iter 10/100: 1.6294619040308345
Iter 20/100: 1.468924904812556
Iter 30/100: 1.4287352233221229
Iter 40/100: 1.3970570330567997
Iter 50/100: 1.3599973879375737
Iter 10/100: 1.6251777947965216
Iter 20/100: 1.4678365214157292
Iter 30/100: 1.429161326955534
Iter 40/100: 1.3998008943779698
Iter 50/100: 1.3669558098154988
Iter 10/100: 1.6197901095231972
Iter 20/100: 1.4655295084378348
Iter 30/100

Iter 30/100: 1.3263906639751073
Iter 40/100: 1.2680640535954086
Iter 50/100: 1.2303703166045707
Iter 60/100: 1.2009751687300072
Iter 70/100: 1.1996500355299797
Iter 80/100: 1.198873445393999
Iter 90/100: 1.1981679010974051
Iter 10/100: 1.515185149654382
Iter 20/100: 1.3981286987524046
Iter 30/100: 1.3230169730459123
Iter 40/100: 1.2641125370601165
Iter 50/100: 1.2264015328460536
Iter 60/100: 1.1975849206475877
Iter 70/100: 1.1962110983100986
Iter 80/100: 1.1954531512073847
Iter 90/100: 1.1947689740722724
Iter 10/100: 1.512806734946217
Iter 20/100: 1.3959538706171506
Iter 30/100: 1.3191123426646587
Iter 40/100: 1.2586763010422768
Iter 50/100: 1.2205435612685926
Iter 60/100: 1.1928954017266258
Iter 70/100: 1.1910932333194482
Iter 80/100: 1.190493959212452
Iter 90/100: 1.1898600799767356
Iter 10/100: 1.5114579826400585
Iter 20/100: 1.3949288118012952
Iter 30/100: 1.3171278013339822
Iter 40/100: 1.2557405375362647
Iter 50/100: 1.2175311880450157
Iter 60/100: 1.1902744552628646
Iter 70/100:

Iter 10/100: 1.4774966394874147
Iter 20/100: 1.3633842409913108
Iter 30/100: 1.2576279947786644
Iter 40/100: 1.168342866693433
Iter 50/100: 1.1433956825260183
Iter 10/100: 1.4770503182630763
Iter 20/100: 1.3629956716385108
Iter 30/100: 1.2562770912413537
Iter 40/100: 1.1658359423619393
Iter 50/100: 1.14118581440814
Iter 10/100: 1.4762057452057769
Iter 20/100: 1.3621438745072147
Iter 30/100: 1.254850489657074
Iter 40/100: 1.1635667031774897
Iter 50/100: 1.1389186449280833
Iter 10/100: 1.4749996751440033
Iter 20/100: 1.360763708724646
Iter 30/100: 1.2524983952185662
Iter 40/100: 1.1606241074284356
Iter 50/100: 1.1358231512647283
Iter 10/100: 1.4742329077791763
Iter 20/100: 1.359952134621574
Iter 30/100: 1.2507454949080923
Iter 40/100: 1.157526036202654
Iter 50/100: 1.1326913388467812
Iter 10/100: 1.4733401917131004
Iter 20/100: 1.3590183427084472
Iter 30/100: 1.249272860217941
Iter 40/100: 1.155219548200838
Iter 50/100: 1.130137726282719
Iter 60/100: 1.1242621909658128
Iter 70/100: 1.122

Iter 60/100: 0.9832448489471391
iteration we acquire top COF =  35
accumulated cost up to observation of top COF =  6021.591684206326  [min]


# Random Search

In [11]:
nb_runs = 1000

rs_res = dict()
rs_res['ids_acquired']     = []
rs_res['cost_acquired']    = []
rs_res['accumulated_cost'] = []

for r in range(nb_runs):
    rs_ids_acquired     = np.random.choice(range(nb_COFs), replace=False, size=nb_iterations)
    rs_cost_acquired    = build_cost(rs_ids_acquired)
    rs_accumulated_cost = accumulated_cost(rs_cost_acquired)
    rs_res['ids_acquired'].append(rs_ids_acquired)
    rs_res['cost_acquired'].append(rs_cost_acquired)
    rs_res['accumulated_cost'].append(rs_accumulated_cost / 60)

In [12]:
def test_rs(rs_res):
    for a in np.random.choice(nb_runs, replace=False, size=7):
        # check that the lengths 
        assert len(rs_res['ids_acquired'][a]) == nb_iterations
        assert all([cof_id in range(nb_COFs) for cof_id in rs_res['ids_acquired'][a]])
    return

test_rs(rs_res)

In [13]:
# get y_max acquired up to iteration i for i = 1,2,...
def y_max(rs_ids_acquired):
    y_max_mu      = np.zeros(nb_iterations)
    y_max_sig_bot = np.zeros(nb_iterations)
    y_max_sig_top = np.zeros(nb_iterations)
    # element i of these will be y max at BO iter i
    
    for i in range(1, nb_iterations+1):
        # max value acquired up to this point
        y_maxes = np.array([max(y[rs_ids_acquired[r][:i]]) for r in range(nb_runs)])
        assert np.size(y_maxes) == nb_runs
        y_max_mu[i-1]      = np.mean(y_maxes)
        y_max_sig_bot[i-1] = np.std(y_maxes[y_maxes < y_max_mu[i-1]])
        y_max_sig_top[i-1] = np.std(y_maxes[y_maxes > y_max_mu[i-1]])
    return y_max_mu, y_max_sig_bot, y_max_sig_top

# rs_mean, rs_lower_bound, rs_upper_bound = y_max(rs_res)
y_rs_max_mu, y_rs_max_sig_bot, y_rs_max_sig_top = y_max(rs_res['ids_acquired'])

In [14]:
###
#  Store Random Search Results
###
random_search_results = dict({'ids_acquired': rs_res['ids_acquired'],
                             'y_rs_max_mu': y_rs_max_mu,
                             'y_rs_max_sig_bot': y_rs_max_sig_bot,
                             'y_rs_max_sig_top': y_rs_max_sig_top,
                             'cost_acquired': rs_res['cost_acquired'],
                             'accumulated_cost': rs_res['accumulated_cost']
                             })

with open('search_results/{}/random_search_results.pkl'.format(normalization), 'wb') as file:
    pickle.dump(random_search_results, file)